In [1]:
import PyPDF2
from typing import Optional
import os
import torch
from accelerate import Accelerator
from transformers import AutoModelForCausalLM, AutoTokenizer

from tqdm.notebook import tqdm
import warnings

from dotenv import load_dotenv
import os

warnings.filterwarnings('ignore')

In [2]:
hf_token = os.getenv("HF_TOKEN")
# print(hf_token)

In [3]:
print(os.path.isfile('../data/2402.13116v4.pdf'))

True


LLaMA model = [meta-llama/Llama-3.2-1B-Instruct](https://huggingface.co/meta-llama/Llama-3.2-1B-Instruct)

In [4]:
pdf_path = '../data/2402.13116v4.pdf'
DEFAULT_MODEL = "meta-llama/Llama-3.2-1B-Instruct"

In [5]:
# Read the file
with open(pdf_path, 'rb') as file:
    pdf_file = file.read()

In [6]:
print(f"Read {len(pdf_file)} bytes from PDF file")

Read 2079796 bytes from PDF file


###  ensure working with a real PDF file that exists

In [7]:
def validate_pdf(file_path: str) -> bool:
    if not os.path.exists(file_path):
        print(f"Error: File not found at path: {file_path}")
        return False
    if not file_path.lower().endswith('.pdf'):
        print("Error: File is not a PDF")
        return False
    return True

### extracts and returns up to max_chars worth of text from a valid PDF file, page by page

In [8]:
def extract_text_from_pdf(file_path: str, max_chars: int = 100000) -> Optional[str]:
    if not validate_pdf(file_path):
        return None
    
    try:
        with open(file_path, 'rb') as file:
            pdf_reader = PyPDF2.PdfReader(file) # Create PDF reader object
            num_pages = len(pdf_reader.pages) # Get total number of pages
            print(f"Processing PDF with {num_pages} pages...")
            
            extracted_text = []
            total_chars = 0
            
            for page_num in range(num_pages): # Iterate through all pages
                page = pdf_reader.pages[page_num] # Extract text from page
                text = page.extract_text()
                
                if total_chars + len(text) > max_chars: # Check if adding this page's text would exceed the limit
                    remaining_chars = max_chars - total_chars # Only add text up to the limit
                    extracted_text.append(text[:remaining_chars]) # add only remaining characters to reach max_chars
                    print(f"Reached {max_chars} character limit at page {page_num + 1}")
                    break
                
                extracted_text.append(text)
                total_chars += len(text)
                print(f"Processed page {page_num + 1}/{num_pages}")
            
            final_text = '\n'.join(extracted_text)
            print(f"\nExtraction complete! Total characters: {len(final_text)}")
            return final_text
            
    except PyPDF2.PdfReadError:
        print("Error: Invalid or corrupted PDF file")
        return None
    except Exception as e:
        print(f"An unexpected error occurred: {str(e)}")
        return None

### fetch metadata

In [9]:
# Get PDF metadata
def get_pdf_metadata(file_path: str) -> Optional[dict]:
    if not validate_pdf(file_path):
        return None
    
    try:
        with open(file_path, 'rb') as file:
            pdf_reader = PyPDF2.PdfReader(file)
            metadata = {
                'num_pages': len(pdf_reader.pages), # total numbers of page numbers
                'metadata': pdf_reader.metadata # any available metadata like title, author, and creation date
            }
            return metadata
    except Exception as e:
        print(f"Error extracting metadata: {str(e)}")
        return None

In [10]:
# Extract metadata first
print("Extracting metadata...")
metadata = get_pdf_metadata(pdf_path)
if metadata:
    print("\nPDF Metadata:")
    print(f"Number of pages: {metadata['num_pages']}")
    print("Document info:")
    for key, value in metadata['metadata'].items():
        print(f"{key}: {value}")

Extracting metadata...

PDF Metadata:
Number of pages: 43
Document info:
/Author: 
/CreationDate: D:20241022021202Z
/Creator: LaTeX with hyperref
/Keywords: 
/ModDate: D:20241022021202Z
/PTEX.Fullbanner: This is pdfTeX, Version 3.141592653-2.6-1.40.25 (TeX Live 2023) kpathsea version 6.3.5
/Producer: pdfTeX-1.40.25
/Subject: 
/Title: 
/Trapped: /False


In [11]:
# Extract text
print("\nExtracting text...")
extracted_text = extract_text_from_pdf(pdf_path)


Extracting text...
Processing PDF with 43 pages...
Processed page 1/43
Processed page 2/43
Processed page 3/43
Processed page 4/43
Processed page 5/43
Processed page 6/43
Processed page 7/43
Processed page 8/43
Processed page 9/43
Processed page 10/43
Processed page 11/43
Processed page 12/43
Processed page 13/43
Processed page 14/43
Processed page 15/43
Processed page 16/43
Reached 100000 character limit at page 17

Extraction complete! Total characters: 100016


In [12]:
# Display first 500 characters of extracted text as preview
if extracted_text:
    print("\nPreview of extracted text (first 500 characters):")
    print("-" * 50) # Prints a visual line divider 
    print(extracted_text[:500])
    print("-" * 50)
    print(f"\nTotal characters extracted: {len(extracted_text)}")


Preview of extracted text (first 500 characters):
--------------------------------------------------
1
A Survey on Knowledge Distillation of Large
Language Models
Xiaohan Xu1, Ming Li2, Chongyang Tao3, Tao Shen4, Reynold Cheng1, Jinyang Li1,
Can Xu5, Dacheng Tao6, Tianyi Zhou2
1The University of Hong Kong2University of Maryland3Microsoft
4University of Technology Sydney5Peking University6The University of Sydney
{shawnxxh,chongyangtao,hishentao }@gmail.com {minglii,tianyi }@umd.edu
ckcheng@cs.hku.hk jl0725@connect.hku.hk
Abstract —In the era of Large Language Models (LLMs), Knowledge Distillati
--------------------------------------------------

Total characters extracted: 100016


In [13]:
# Optional: Save the extracted text to a file
if extracted_text:
    output_file = '../data/extracted_text.txt'
    with open(output_file, 'w', encoding='utf-8') as f:
        f.write(extracted_text)
    print(f"\nExtracted text has been saved to {output_file}")


Extracted text has been saved to ../data/extracted_text.txt


In [14]:
device = "cuda" if torch.cuda.is_available() else "cpu"

SYS_PROMPT = """
You are a world class text pre-processor, here is the raw data from a PDF, please parse and return it in a way that is crispy and usable to send to a podcast writer.

The raw data is messed up with new lines, Latex math and you will see fluff that we can remove completely. Basically take away any details that you think might be useless in a podcast author's transcript.

Remember, the podcast could be on any topic whatsoever so the issues listed above are not exhaustive

Please be smart with what you remove and be creative ok?

Remember DO NOT START SUMMARIZING THIS, YOU ARE ONLY CLEANING UP THE TEXT AND RE-WRITING WHEN NEEDED

Be very smart and aggressive with removing details, you will get a running portion of the text and keep returning the processed text.

PLEASE DO NOT ADD MARKDOWN FORMATTING, STOP ADDING SPECIAL CHARACTERS THAT MARKDOWN CAPATILISATION ETC LIKES

ALWAYS start your response directly with processed text and NO ACKNOWLEDGEMENTS about my questions ok?
Here is the text:
"""

### Split Text into Chunks at Word Boundaries (Close to Target Size)

Example Input:
text = "The quick brown fox jumps over the lazy dog"
target_chunk_size = 15

Output Chunks:
chunks = [
  "The quick",         # 9 chars → next word "brown" (5+1) would make 15 → hit limit → start new chunk
  "brown fox",         # 9 chars → next word "jumps" would exceed 15 → start new chunk
  "jumps over the",    # 14 chars → next word "lazy" would exceed 15 → start new chunk
  "lazy dog"           # 8 chars → remaining words
]


In [15]:
def create_word_bounded_chunks(text, target_chunk_size):
    """
    Split text into chunks at word boundaries close to the target chunk size.
    """
    words = text.split() # Example: "hello world amazing" ➝ ['hello', 'world', 'amazing']
    chunks = []
    current_chunk = []
    current_length = 0
    
    for word in words:
        word_length = len(word) + 1  # +1 for the space
        if current_length + word_length > target_chunk_size and current_chunk:
            # Join the current chunk and add it to chunks
            chunks.append(' '.join(current_chunk))
            current_chunk = [word]
            current_length = word_length
        else:
            current_chunk.append(word)
            current_length += word_length
    
    # Add the last chunk if it exists
    if current_chunk:
        chunks.append(' '.join(current_chunk))
    
    return chunks

In [16]:
pdf_file

b'%PDF-1.5\n%\x8f\n7 0 obj\n<< /Type /XObject /Subtype /Form /BBox [ 0 0 100 100 ]\n/Filter /FlateDecode /FormType 1 /Length 15\n/Matrix [ 1 0 0 1 0 0 ] /Resources 8 0 R >>\nstream\nx\xda\xd3\x0f\xceP(\xce\xe0\x02\x00\x07\xfd\x01\xf0endstream\nendobj\n9 0 obj\n<< /Type /XObject /Subtype /Form /BBox [ 0 0 100 100 ]\n/Filter /FlateDecode /FormType 1 /Length 15\n/Matrix [ 1 0 0 1 0 0 ] /Resources 10 0 R >>\nstream\nx\xda\xd3\x0f\xceP(\xce\xe0\x02\x00\x07\xfd\x01\xf0endstream\nendobj\n11 0 obj\n<< /Type /XObject /Subtype /Form /BBox [ 0 0 100 100 ]\n/Filter /FlateDecode /FormType 1 /Length 15\n/Matrix [ 1 0 0 1 0 0 ] /Resources 12 0 R >>\nstream\nx\xda\xd3\x0f\xceP(\xce\xe0\x02\x00\x07\xfd\x01\xf0endstream\nendobj\n17 0 obj\n<< /Type /XObject /Subtype /Form /BBox [ 0 0 100 100 ]\n/Filter /FlateDecode /FormType 1 /Length 15\n/Matrix [ 1 0 0 1 0 0 ] /Resources 18 0 R >>\nstream\nx\xda\xd3\x0f\xceP(\xce\xe0\x02\x00\x07\xfd\x01\xf0endstream\nendobj\n20 0 obj\n<< /Type /XObject /Subtype /Form /

###  creates an Accelerator object from the Hugging Face accelerate library to manage running models efficiently on different hardware setups (like CPU, GPU, or multiple GPUs) without needing to write complex device-handling code

In [17]:
accelerator = Accelerator()
model = AutoModelForCausalLM.from_pretrained(
    DEFAULT_MODEL,
    use_auth_token=hf_token,
    torch_dtype=torch.bfloat16,
    use_safetensors=True,
    device_map=device,
)
tokenizer = AutoTokenizer.from_pretrained(DEFAULT_MODEL, use_safetensors=True) # converts text to numbers(tokens) 
model, tokenizer = accelerator.prepare(model, tokenizer)

C:\Users\<username>\.cache\huggingface\hub

In [ ]:
from transformers.utils import default_cache_path
print(default_cache_path)

### Basically, this `process_chunk()` function is to cleans, polishes, and lightly rewrites raw messy PDF text.

In [18]:
def process_chunk(text_chunk, chunk_num):
    """Process a chunk of text and return both input and output for verification"""
    conversation = [
        {"role": "system", "content": SYS_PROMPT},
        {"role": "user", "content": text_chunk},
    ]


    # tokenize=False means this returns the plain text prompt, not tokenized yet.
    prompt = tokenizer.apply_chat_template(conversation, tokenize=False)
    # prompt text is tokenized into input IDs (numbers the model understands)
    # return_tensors="pt" converts it to PyTorch tensors, ready for the model.
    # .to(device) moves the tensors to your GPU or CPU.
    inputs = tokenizer(prompt, return_tensors="pt").to(device) 
    
    with torch.no_grad(): # runs model’s text generation process without tracking gradients (no training, just inference).
        output = model.generate(
            **inputs,
            temperature=0.7, #  controls randomness (lower → more deterministic).
            top_p=0.9,
            max_new_tokens=512 # limits output length.
        )
    
    processed_text = tokenizer.decode(output[0], skip_special_tokens=True)[len(prompt):].strip()
    # Decodes the generated token IDs back into readable text.
    # skip_special_tokens=True removes tokens like <pad>, <eos>.
    # [len(prompt):] removes the original prompt from the generated output — leaving just what the model newly generated.
    # .strip() cleans up whitespace.
    
    # Print chunk information for monitoring
    #print(f"\n{'='*40} Chunk {chunk_num} {'='*40}")
    print(f"INPUT TEXT:\n{text_chunk[:500]}...")  # Show first 500 chars of input
    print(f"\nPROCESSED TEXT:\n{processed_text[:500]}...")  # Show first 500 chars of output
    print(f"{'='*90}\n")
    
    return processed_text

In [19]:
INPUT_FILE = "../data/extracted_text.txt"  # Replace with your file path
CHUNK_SIZE = 1000  # Adjust chunk size if needed

# Read the file
with open(INPUT_FILE, 'r', encoding='utf-8') as file:
    text = file.read()

# Calculate number of chunks
num_chunks = (len(text) + CHUNK_SIZE - 1) // CHUNK_SIZE
num_chunks

101

In [20]:
# Create output file name
output_dir = '../data'
processed_text = ""
os.makedirs(output_dir, exist_ok=True)
output_file = os.path.join(output_dir, f"clean_{os.path.basename(INPUT_FILE)}")

In [21]:
output_file

'../data\\clean_extracted_text.txt'

In [22]:
chunks = create_word_bounded_chunks(text, CHUNK_SIZE)
chunks[1]

'advanced knowledge to smaller models and its utility in model compression and self- improvement. Our survey is meticulously structured around three foundational pillars: algorithm ,skill, and verticalization – providing a comprehensive examination of KD mechanisms, the enhancement of specific cognitive abilities, and their practical implications across diverse fields. Crucially, the survey navigates the interaction between data augmentation (DA) and KD, illustrating how DA emerges as a powerful paradigm within the KD framework to bolster LLMs’ performance. By leveraging DA to generate context-rich, skill- specific training data, KD transcends traditional boundaries, enabling open-source models to approximate the contextual adeptness, ethical alignment, and deep semantic insights characteristic of their proprietary counterparts. This work aims to provide an insightful guide for researchers and practitioners, offering a detailed overview of current methodologies in knowledge'

In [23]:
num_chunks = len(chunks)
num_chunks

101

In [24]:
with open(output_file, 'w', encoding='utf-8') as out_file:
    for chunk_num, chunk in enumerate(tqdm(chunks, desc="Processing chunks")):
        # Process chunk and append to complete text
        processed_chunk = process_chunk(chunk, chunk_num)
        processed_text += processed_chunk + "\n"
        
        # Write chunk immediately to file
        out_file.write(processed_chunk + "\n")
        out_file.flush()

Processing chunks:   0%|          | 0/101 [00:00<?, ?it/s]

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


INPUT TEXT:
1 A Survey on Knowledge Distillation of Large Language Models Xiaohan Xu1, Ming Li2, Chongyang Tao3, Tao Shen4, Reynold Cheng1, Jinyang Li1, Can Xu5, Dacheng Tao6, Tianyi Zhou2 1The University of Hong Kong2University of Maryland3Microsoft 4University of Technology Sydney5Peking University6The University of Sydney {shawnxxh,chongyangtao,hishentao }@gmail.com {minglii,tianyi }@umd.edu ckcheng@cs.hku.hk jl0725@connect.hku.hk Abstract —In the era of Large Language Models (LLMs), Knowledge Distillati...

PROCESSED TEXT:
...



Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


...

INPUT TEXT:
‘reflection to- kens.’ For instance, Self-Rag initiates the retrieval operation when generating the reflection token Retrieve . To distill this critic data, GPT-4 is prompted to assess the need for retrieval using few-shot demonstrations I, the task input x, and output yto predict a reflection token ras follows: p(r|I, x, y ). 4.2 Alignment 4.2.1 Thinking Pattern Most existing methods mainly focus on directly aligning the direct responses of the student models to the responses of teacher models ...

PROCESSED TEXT:
eval using few-shot demonstrations I, the task input x, and output y to predict a reflection token ras follows: p(r|I, x, y). 4.2.1 Thinking Pattern Most existing methods mainly focus on directly aligning the direct responses of the student models to the responses of teacher models though effective they might suffer the problems they tend to learn to imitate the response style of the teacher models but not the reasoning process. Thus in order to better distill fr

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


INPUT TEXT:
by the effectiveness of LLMs in generat- ing their own feedback without relying on external mod- els (Schick et al., 2022; Madaan et al., 2023; Saunders et al., 2022), SelFee (Ye et al., 2023) proposes to train a 17 model that has been fine-tuned to continuously revise its own answer until it provides a high-quality response in a single inference. During training, it utilizes both the final response and feedback chain as the fitting target. This pat- tern, response with the revision process, sho...

PROCESSED TEXT:
SelFee proposes a model that fine-tunes itself to continuously revise its answer until it provides a high-quality response in a single inference. During training, it utilizes the final response and feedback chain as the target. This pattern, response with the revision process, shows a promising performance gain. Following SelFee, Reflection-Tuning also utilizes the reflection process as the learning pattern. Noticing the lack of reasoning imitation of previous me

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


INPUT TEXT:
experiments verify the effectiveness of distilling with this thinking pattern. The following Orca2 (Mitra et al., 2023) further presents to equip the student models with the ability to utilize different solution strategies for different tasks, mo- tivated by the capability discrepancies between the smaller and larger models. By employing this training pattern, the student models are able to gain a better reasoning ability. Be- sides learning with the corresponding revision or reflection process,...

PROCESSED TEXT:
his thinking pattern. The Orca2 (Mitra et al., 2023) study demonstrates the ability of student models to utilize different problem-solving strategies for various tasks, motivated by discrepancies between smaller and larger models. By employing this training approach, student models gain a better reasoning ability.

Sides learning with the corresponding revision or reflection process, another thinking pattern that recently emerged is generating both responses and 

In [25]:
print(f"\nProcessing complete!")
print(f"Input file: {INPUT_FILE}")
print(f"Output file: {output_file}")
print(f"Total chunks processed: {num_chunks}")


Processing complete!
Input file: ../data/extracted_text.txt
Output file: ../data\clean_extracted_text.txt
Total chunks processed: 101


In [26]:
# Preview the beginning and end of the complete processed text
print("\nPreview of final processed text:")
print("\nBEGINNING:")
print(processed_text[:1000])
print("\n...\n\nEND:")
print(processed_text[-1000:])


Preview of final processed text:

BEGINNING:

odel compression and self-improvement is a topic of great interest. A meticulously structured survey examines three foundational pillars: algorithm, skill, and verticalization, providing a comprehensive examination of knowledge distillation mechanisms, the enhancement of specific cognitive abilities, and their practical implications across diverse fields. Crucially, the survey explores the interaction between data augmentation and knowledge distillation, demonstrating how data augmentation emerges as a powerful paradigm within the knowledge distillation framework to bolster large language models' performance. By leveraging data augmentation to generate context-rich, skill-specific training data, knowledge distillation transcends traditional boundaries, enabling open-source models to approximate the contextual adeptness, ethical alignment, and deep semantic insights characteristic of proprietary models. This work aims to provide a detailed 